In [1]:
import sys
sys.path.append('C:\\Users\marti\Anaconda3\Lib\site-packages')

In [2]:
import numpy as np 
import pandas as pd 
import tensorflow
import nltk
import os
import gc
from keras.preprocessing import sequence,text
from keras.preprocessing.text import Tokenizer
from keras.models import Sequential
from keras.layers import Dense,Dropout,Embedding,LSTM,Conv1D,GlobalMaxPooling1D,Flatten,MaxPooling1D,GRU,SpatialDropout1D,Bidirectional
from keras.callbacks import EarlyStopping
from keras.utils import to_categorical
from keras.losses import categorical_crossentropy
from keras.optimizers import Adam
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score,confusion_matrix,classification_report,f1_score
import matplotlib.pyplot as plt
import warnings
warnings.filterwarnings("ignore")
#pd.set_option('display.max_colwidth',100)
pd.set_option('display.max_colwidth', -1)

Using TensorFlow backend.


In [3]:
os.getcwd()
os.chdir('C:\\Users\\marti\\Documents\\rt_sent_data')
print(os.listdir())

['.ipynb_checkpoints', 'lexicon.pickle', 'model.ckpt.data-00000-of-00001', 'model.ckpt.index', 'model.ckpt.meta', 'Model_full_training_data_basic_nn', 'Model_training_data', 'sampleSubmission.csv', 'Sentiment_analysis_nn.ipynb', 'test.tsv', 'test_df.pkl', 'test_set.txt', 'tf.log', 'train.tsv', 'train_df.pkl', 'train_set.txt']


In [4]:
import gc
pd.set_option('display.max_colwidth', 100)

In [5]:
gc.collect()

7

In [6]:
train=pd.read_csv('..\\rt_sent_data\\train.tsv',sep='\t')
print(train.shape)
train.head()

(156060, 4)


PhraseId  SentenceId  \
0         1           1   
1         2           1   
2         3           1   
3         4           1   
4         5           1   

                                                                                                Phrase  \
0  A series of escapades demonstrating the adage that what is good for the goose is also good for t...   
1                        A series of escapades demonstrating the adage that what is good for the goose   
2                                                                                             A series   
3                                                                                                    A   
4                                                                                               series   

   Sentiment  
0          1  
1          2  
2          2  
3          2  
4          2

In [7]:
test=pd.read_csv('..\\rt_sent_data\\test.tsv',sep='\t')
print(test.shape)
test.head()

(66292, 3)


PhraseId  SentenceId  \
0    156061        8545   
1    156062        8545   
2    156063        8545   
3    156064        8545   
4    156065        8545   

                                                   Phrase  
0  An intermittently pleasing but mostly routine effort .  
1    An intermittently pleasing but mostly routine effort  
2                                                      An  
3       intermittently pleasing but mostly routine effort  
4              intermittently pleasing but mostly routine

In [8]:
sub=pd.read_csv('..\\rt_sent_data\\sampleSubmission.csv')
sub.head()

PhraseId  Sentiment
0    156061          2
1    156062          2
2    156063          2
3    156064          2
4    156065          2

In [9]:
test['Sentiment']=-999
test.head()

PhraseId  SentenceId  \
0    156061        8545   
1    156062        8545   
2    156063        8545   
3    156064        8545   
4    156065        8545   

                                                   Phrase  Sentiment  
0  An intermittently pleasing but mostly routine effort .       -999  
1    An intermittently pleasing but mostly routine effort       -999  
2                                                      An       -999  
3       intermittently pleasing but mostly routine effort       -999  
4              intermittently pleasing but mostly routine       -999

In [10]:
df=pd.concat([train,test], ignore_index=True)
print(df.shape)
df.tail()

(222352, 4)


PhraseId  SentenceId                                  Phrase  \
222347    222348       11855  A long-winded , predictable scenario .   
222348    222349       11855    A long-winded , predictable scenario   
222349    222350       11855                         A long-winded ,   
222350    222351       11855                           A long-winded   
222351    222352       11855                    predictable scenario   

        Sentiment  
222347       -999  
222348       -999  
222349       -999  
222350       -999  
222351       -999

In [11]:
del train,test
gc.collect()

0

In [12]:
from nltk.tokenize import word_tokenize
from nltk.stem import SnowballStemmer,WordNetLemmatizer
stemmer=SnowballStemmer('english')
lemma=WordNetLemmatizer()
from string import punctuation
import re
from bs4 import BeautifulSoup

In [13]:
def clean_review(review_col):
    review_corpus=[]
    for i in range(0,len(review_col)):
        review=str(review_col[i])
        review=re.sub('[^a-zA-Z]',' ',review)
        review=[lemma.lemmatize(w) for w in word_tokenize(str(review).lower())]
        review = ' '.join(review)
        review_corpus.append(review)
    return review_corpus

In [14]:
df['clean_review']=clean_review(df.Phrase.values)
df.head()

PhraseId  SentenceId  \
0         1           1   
1         2           1   
2         3           1   
3         4           1   
4         5           1   

                                                                                                Phrase  \
0  A series of escapades demonstrating the adage that what is good for the goose is also good for t...   
1                        A series of escapades demonstrating the adage that what is good for the goose   
2                                                                                             A series   
3                                                                                                    A   
4                                                                                               series   

   Sentiment  \
0          1   
1          2   
2          2   
3          2   
4          2   

                                                                                          clean_review  
0  a series of escapade demonstrating the adage that what is good for the goose is also good for th...  
1                         a series of escapade demonstrating the adage that what is good for the goose  
2                                                                                             a series  
3                                                                                                    a  
4                                                                                               series

In [15]:
df_train=df[df.Sentiment !=-999]
df_train.shape

(156060, 5)

In [16]:
df_test=df[df.Sentiment==-999]
df_test.drop('Sentiment', axis=1, inplace=True)
print(df_test.shape)
df_test.head()

(66292, 4)


PhraseId  SentenceId  \
156060    156061        8545   
156061    156062        8545   
156062    156063        8545   
156063    156064        8545   
156064    156065        8545   

                                                        Phrase  \
156060  An intermittently pleasing but mostly routine effort .   
156061    An intermittently pleasing but mostly routine effort   
156062                                                      An   
156063       intermittently pleasing but mostly routine effort   
156064              intermittently pleasing but mostly routine   

                                                clean_review  
156060  an intermittently pleasing but mostly routine effort  
156061  an intermittently pleasing but mostly routine effort  
156062                                                    an  
156063     intermittently pleasing but mostly routine effort  
156064            intermittently pleasing but mostly routine

In [17]:
df_train.head()

PhraseId  SentenceId  \
0         1           1   
1         2           1   
2         3           1   
3         4           1   
4         5           1   

                                                                                                Phrase  \
0  A series of escapades demonstrating the adage that what is good for the goose is also good for t...   
1                        A series of escapades demonstrating the adage that what is good for the goose   
2                                                                                             A series   
3                                                                                                    A   
4                                                                                               series   

   Sentiment  \
0          1   
1          2   
2          2   
3          2   
4          2   

                                                                                          clean_review  
0  a series of escapade demonstrating the adage that what is good for the goose is also good for th...  
1                         a series of escapade demonstrating the adage that what is good for the goose  
2                                                                                             a series  
3                                                                                                    a  
4                                                                                               series

In [18]:
from keras.utils import to_categorical
train_text=df_train.clean_review.values
test_text=df_test.clean_review.values
target=df_train.Sentiment.values
y = to_categorical(target)
print(train_text.shape,target.shape,y.shape)

(156060,) (156060,) (156060, 5)


In [19]:
from sklearn.model_selection import train_test_split
X_train_text,X_val_text,y_train,y_val=train_test_split(train_text,y,test_size=0.2,stratify=y,random_state=123)
print(X_train_text.shape,y_train.shape)
print(X_val_text.shape,y_val.shape)

(124848,) (124848, 5)
(31212,) (31212, 5)


In [20]:
all_words = ' '.join(X_train_text)
all_words=word_tokenize(all_words)
dist = nltk.FreqDist(all_words)
num_unique_word = len(dist)
num_unique_word

13732

In [21]:
r_len = []
for text in X_train_text:
    word = word_tokenize(text)
    l = len(word)
    r_len.append(l)

MAX_REVIEW_LEN=np.max(r_len)
MAX_REVIEW_LEN

48

In [22]:
max_features = num_unique_word
max_words = MAX_REVIEW_LEN
batch_size = 128
epochs = 3
num_classes = 5

In [23]:
tokenizer = Tokenizer(num_words=max_features)
tokenizer.fit_on_texts(list(X_train_text))
X_train = tokenizer.texts_to_sequences(X_train_text)
X_val = tokenizer.texts_to_sequences(X_val_text)
X_test = tokenizer.texts_to_sequences(test_text)

In [24]:
X_train = sequence.pad_sequences(X_train, maxlen=max_words)
X_val = sequence.pad_sequences(X_val, maxlen=max_words)
X_test = sequence.pad_sequences(X_test, maxlen=max_words)
print(X_train.shape, X_val.shape, X_test.shape)

(124848, 48) (31212, 48) (66292, 48)


In [31]:
model=Sequential()
model.add(Embedding(input_dim = max_features,output_dim=128))
model.add(Dropout(0.2))
model.add(Conv1D(64, 5, activation='relu'))
model.add(MaxPooling1D(pool_size=4))
model.add(LSTM(64,dropout=0.2, recurrent_dropout=0.2,return_sequences=True))
model.add(LSTM(32,dropout=0.5, recurrent_dropout=0.5,return_sequences=False))
model.add(Dense(num_classes,activation='softmax'))
model.compile(loss='categorical_crossentropy', optimizer=Adam(lr=0.001), metrics=['accuracy'])
model.summary()

_________________________________________________________________
Layer (type)                 Output Shape              Param #   
embedding_6 (Embedding)      (None, None, 128)         1757696   
_________________________________________________________________
dropout_6 (Dropout)          (None, None, 128)         0         
_________________________________________________________________
conv1d_6 (Conv1D)            (None, None, 64)          41024     
_________________________________________________________________
max_pooling1d_2 (MaxPooling1 (None, None, 64)          0         
_________________________________________________________________
lstm_3 (LSTM)                (None, None, 64)          33024     
_________________________________________________________________
lstm_4 (LSTM)                (None, 32)                12416     
_________________________________________________________________
dense_2 (Dense)              (None, 5)                 165       
Total para

In [30]:
history1=model.fit(X_train, y_train, validation_data=(X_val, y_val),epochs=epochs, batch_size=batch_size, verbose=1)

Train on 124848 samples, validate on 31212 samples
Epoch 1/3
124848/124848 [==============================] - 112s 899us/step - loss: 1.1267 - acc: 0.5503 - val_loss: 1.0019 - val_acc: 0.6066
Epoch 2/3
124848/124848 [==============================] - 99s 791us/step - loss: 0.8801 - acc: 0.6475 - val_loss: 0.8426 - val_acc: 0.6555
Epoch 3/3
124848/124848 [==============================] - 91s 730us/step - loss: 0.7696 - acc: 0.6895 - val_loss: 0.8232 - val_acc: 0.6613


In [32]:
y_pred1=model1.predict_classes(X_test,verbose=1)

66292/66292 [==============================] - 39s 593us/step


In [52]:
y_pred1

array([2, 2, 2, ..., 1, 1, 1], dtype=int64)

In [49]:
sub.Sentiment=y_pred1
for ident, line, rating in zip(df_test.PhraseId, df_test.Phrase, sub.Sentiment):
    if rating == 0:
        result = 'negative'
    elif rating == 1:
        result = 'somewhat negative'
    elif rating == 2:
        result = 'neutral'
    elif rating == 3:
        result = 'somewhat positive'
    elif rating == 4:
        result = 'postive'
    print(str(ident) + ': ' + line + ' Rating:' + result)

156061: An intermittently pleasing but mostly routine effort . Rating:neutral
156062: An intermittently pleasing but mostly routine effort Rating:neutral
156063: An Rating:neutral
156064: intermittently pleasing but mostly routine effort Rating:neutral
156065: intermittently pleasing but mostly routine Rating:neutral
156066: intermittently pleasing but Rating:somewhat positive
156067: intermittently pleasing Rating:somewhat positive
156068: intermittently Rating:neutral
156069: pleasing Rating:somewhat positive
156070: but Rating:neutral
156071: mostly routine Rating:neutral
156072: mostly Rating:neutral
156073: routine Rating:neutral
156074: effort Rating:neutral
156075: . Rating:neutral
156076: Kidman is really the only thing that 's worth watching in Birthday Girl , a film by the stage-trained Jez Butterworth -LRB- Mojo -RRB- that serves as yet another example of the sad decline of British comedies in the post-Full Monty world . Rating:somewhat positive
156077: Kidman Rating:neutral

157366: fuse Rating:neutral
157367: the two ` woods ' Rating:neutral
157368: the two Rating:neutral
157369: two Rating:neutral
157370: ` woods ' Rating:neutral
157371: woods ' Rating:neutral
157372: woods Rating:neutral
157373: winds up a Bolly-Holly masala mess Rating:negative
157374: winds up Rating:neutral
157375: winds Rating:neutral
157376: a Bolly-Holly masala mess Rating:negative
157377: Bolly-Holly masala mess Rating:somewhat negative
157378: Bolly-Holly Rating:neutral
157379: masala mess Rating:negative
157380: masala Rating:neutral
157381: mess Rating:negative
157382: Though of particular interest to students and enthusiast of international dance and world music , the film is designed to make viewers of all ages , cultural backgrounds and rhythmic ability want to get up and dance . Rating:somewhat positive
157383: Though of particular interest to students and enthusiast of international dance and world music , the film is designed to make viewers of all ages Rating:somewhat p

158365: whose few T&A bits Rating:neutral
158366: whose few Rating:neutral
158367: whose Rating:neutral
158368: T&A bits Rating:neutral
158369: T&A Rating:neutral
158370: bits Rating:neutral
158371: still ca n't save itself from being unoriginal , unfunny and unrecommendable . Rating:somewhat negative
158372: ca n't save itself from being unoriginal , unfunny and unrecommendable . Rating:somewhat negative
158373: ca n't save itself from being unoriginal , unfunny and unrecommendable Rating:somewhat negative
158374: save itself from being unoriginal , unfunny and unrecommendable Rating:somewhat negative
158375: save itself Rating:neutral
158376: save Rating:neutral
158377: itself Rating:neutral
158378: from being unoriginal , unfunny and unrecommendable Rating:somewhat negative
158379: being unoriginal , unfunny and unrecommendable Rating:somewhat negative
158380: unoriginal , unfunny and unrecommendable Rating:negative
158381: unoriginal Rating:somewhat negative
158382: , unfunny and u

159365: a big middle-fingered `` shut up '' to those who talk up what is nothing more than two guys beating the hell outta Rating:somewhat negative
159366: a big middle-fingered `` Rating:neutral
159367: a big middle-fingered Rating:neutral
159368: big middle-fingered Rating:neutral
159369: middle-fingered Rating:neutral
159370: shut up '' to those who talk up what is nothing more than two guys beating the hell outta Rating:somewhat negative
159371: shut up '' Rating:neutral
159372: shut up Rating:neutral
159373: shut Rating:neutral
159374: to those who talk up what is nothing more than two guys beating the hell outta Rating:somewhat negative
159375: those who talk up what is nothing more than two guys beating the hell outta Rating:somewhat negative
159376: who talk up what is nothing more than two guys beating the hell outta Rating:somewhat negative
159377: talk up what is nothing more than two guys beating the hell outta Rating:somewhat negative
159378: talk up Rating:neutral
159379:

160364: art house screens Rating:neutral
160365: house screens Rating:neutral
160366: house Rating:neutral
160367: screens Rating:neutral
160368: for no reason other Rating:neutral
160369: no reason other Rating:neutral
160370: reason other Rating:neutral
160371: reason Rating:neutral
160372: than the fact Rating:neutral
160373: the fact Rating:neutral
160374: fact Rating:neutral
160375: that it 's in French -LRB- well , mostly -RRB- with English subtitles Rating:neutral
160376: it 's in French -LRB- well , mostly -RRB- with English subtitles Rating:neutral
160377: 's in French -LRB- well , mostly -RRB- with English subtitles Rating:neutral
160378: in French -LRB- well , mostly -RRB- with English subtitles Rating:neutral
160379: French -LRB- well , mostly -RRB- with English subtitles Rating:neutral
160380: French -LRB- well , mostly -RRB- Rating:neutral
160381: French Rating:neutral
160382: -LRB- well , mostly -RRB- Rating:neutral
160383: well , mostly -RRB- Rating:somewhat positive
16

...

216837: naptime Rating:neutral
216838: ... Hudlin is stuck trying to light a fire with soggy leaves . Rating:negative
216839: Hudlin is stuck trying to light a fire with soggy leaves . Rating:negative
216840: is stuck trying to light a fire with soggy leaves . Rating:negative
216841: is stuck trying to light a fire with soggy leaves Rating:negative
216842: stuck trying to light a fire with soggy leaves Rating:somewhat negative
216843: trying to light a fire with soggy leaves Rating:somewhat negative
216844: to light a fire with soggy leaves Rating:somewhat negative
216845: light a fire with soggy leaves Rating:somewhat negative
216846: light a fire Rating:neutral
216847: a fire Rating:neutral
216848: with soggy leaves Rating:somewhat negative
216849: soggy leaves Rating:somewhat negative
216850: The film is exhilarating to watch because Sandler , liberated from the constraints of formula , reveals unexpected depths as an actor . Rating:postive
216851: is exhilarating to watch because S

217837: An earnest , heartrending look at the divide between religious fundamentalists and their gay relatives Rating:somewhat positive
217838: An earnest , Rating:somewhat positive
217839: An earnest Rating:somewhat positive
217840: heartrending look at the divide between religious fundamentalists and their gay relatives Rating:neutral
217841: heartrending look Rating:neutral
217842: heartrending Rating:neutral
217843: at the divide between religious fundamentalists and their gay relatives Rating:neutral
217844: the divide between religious fundamentalists and their gay relatives Rating:neutral
217845: the divide Rating:neutral
217846: between religious fundamentalists and their gay relatives Rating:neutral
217847: religious fundamentalists and their gay relatives Rating:neutral
217848: religious fundamentalists and Rating:neutral
217849: religious fundamentalists Rating:neutral
217850: fundamentalists Rating:neutral
217851: their gay relatives Rating:neutral
217852: gay relatives Rat

219336: the thrall of a vicious hangover Rating:neutral
219337: the thrall Rating:neutral
219338: thrall Rating:neutral
219339: of a vicious hangover Rating:neutral
219340: a vicious hangover Rating:neutral
219341: vicious hangover Rating:neutral
219342: vicious Rating:neutral
219343: hangover Rating:neutral
219344: Tadpole is emblematic of the witless ageism afflicting films : Young is cool , and too young is too cool . Rating:somewhat negative
219345: Tadpole is emblematic of the witless ageism afflicting films : Young is cool , and too young is too cool Rating:somewhat negative
219346: Tadpole is emblematic of the witless ageism afflicting films : Rating:somewhat negative
219347: Tadpole is emblematic of the witless ageism afflicting films Rating:somewhat negative
219348: is emblematic of the witless ageism afflicting films Rating:somewhat negative
219349: is emblematic of the witless ageism Rating:somewhat negative
219350: emblematic of the witless ageism Rating:somewhat negative
2

220336: it 's more of the same Rating:neutral
220337: 's more of the same Rating:neutral
220338: more of the same Rating:neutral
220339: of the same Rating:neutral
220340: as the film proves , that 's not always a bad thing Rating:somewhat negative
220341: as the film proves Rating:neutral
220342: the film proves Rating:neutral
220343: , that 's not always a bad thing Rating:somewhat negative
220344: that 's not always a bad thing Rating:somewhat negative
220345: 's not always a bad thing Rating:somewhat negative
220346: 's not always Rating:neutral
220347: With Spy Kids 2 : The Island of Lost Dreams writer\/director\/producer Robert Rodriguez has cobbled together a film that feels like a sugar high gone awry . Rating:somewhat negative
220348: With Spy Kids 2 Rating:neutral
220349: Spy Kids 2 Rating:neutral
220350: Kids 2 Rating:neutral
220351: : The Island of Lost Dreams writer\/director\/producer Robert Rodriguez has cobbled together a film that feels like a sugar high gone awry . Ra

221835: is lame Rating:somewhat negative
221836: And that leaves a hole in the center of The Salton Sea . Rating:somewhat negative
221837: that leaves a hole in the center of The Salton Sea . Rating:somewhat negative
221838: leaves a hole in the center of The Salton Sea . Rating:somewhat negative
221839: leaves a hole in the center of The Salton Sea Rating:somewhat negative
221840: a hole in the center of The Salton Sea Rating:somewhat negative
221841: a hole Rating:somewhat negative
221842: in the center of The Salton Sea Rating:neutral
221843: the center of The Salton Sea Rating:neutral
221844: of The Salton Sea Rating:neutral
221845: The Salton Sea Rating:neutral
221846: Salton Sea Rating:neutral
221847: Salton Rating:neutral
221848: There 's no mistaking the fact that this hybrid misses the impact of the Disney classic , and even that of the excellent 1934 MGM version . Rating:somewhat negative
221849: 's no mistaking the fact that this hybrid misses the impact of the Disney classi

In [50]:
sub.to_csv('sub.csv',index=False)
sub

PhraseId  Sentiment
0        156061          2
1        156062          2
2        156063          2
3        156064          2
4        156065          2
5        156066          3
6        156067          3
7        156068          2
8        156069          3
9        156070          2
10       156071          2
11       156072          2
12       156073          2
13       156074          2
14       156075          2
15       156076          3
16       156077          2
17       156078          3
18       156079          3
19       156080          2
20       156081          2
21       156082          2
22       156083          3
23       156084          2
24       156085          2
25       156086          2
26       156087          2
27       156088          2
28       156089          3
29       156090          2
...         ...        ...
66262    222323          2
66263    222324          2
66264    222325          2
66265    222326          3
66266    222327          3
66267    222328          3
66268    222329          2
66269    222330          2
66270    222331          2
66271    222332          2
66272    222333          2
66273    222334          2
66274    222335          2
66275    222336          2
66276    222337          2
66277    222338          2
66278    222339          2
66279    222340          2
66280    222341          1
66281    222342          1
66282    222343          1
66283    222344          2
66284    222345          2
66285    222346          2
66286    222347          2
66287    222348          0
66288    222349          0
66289    222350          1
66290    222351          1
66291    222352          1

[66292 rows x 2 columns]